In [1]:
using Profile
using ProfileCanvas
using BenchmarkTools

In [2]:
using Distributions

function sim_t_test(; dist = Normal(), n = 10, μ = mean(dist), L = 10^5)
    pval = Float64[]
    for _ in 1:L
        X = rand(dist, n)
        X̄ = mean(X)
        S = std(X)
        t = √n * (X̄ - μ)/S
        p = 2ccdf(TDist(n-1), abs(t))
        push!(pval, p)
    end
    pval
end

pval = @time sim_t_test(L=100)
pval = @time sim_t_test(L=100)
pval = @time sim_t_test(L=100)
pval = @btime sim_t_test(L=100);

  0.000074 seconds (104 allocations: 15.984 KiB)
  0.000048 seconds (104 allocations: 15.984 KiB)
  0.000047 seconds (104 allocations: 15.984 KiB)
  32.700 μs (104 allocations: 15.98 KiB)


In [3]:
@profview_allocs sim_t_test(L=100) sample_rate=1

ProfileCanvas.ProfileData(Dict{String, ProfileCanvas.ProfileFrame}("count" => ProfileCanvas.ProfileFrame("root", "", "", 0, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#15", "task.jl", ".\\task.jl", 484, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eventloop", "eventloop.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\eventloop.jl", 8, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("invokelatest", "essentials.jl", ".\\essentials.jl", 726, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#invokelatest#2", "essentials.jl", ".\\essentials.jl", 729, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("execute_request", "execute_request.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\execute_request.jl", 67, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("softscope_include_string", "SoftGlobalScope.jl", "D:\\.julia\\packages\\SoftGlobalScope\\u4UzH\\src\\SoftGlobalScope.jl", 65, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("include_string", "loading.jl", ".\\loading.jl", 1428, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eval", "boot.jl", ".\\boot.jl", 368, 130, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("Tuple{Symbol}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.SimpleVector", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("DataType", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("UnionAll", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Tuple{Int64}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("UnknownType", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.CodeInfo", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Vector{UInt8}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("CorruptType", "", "", 0, 5, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Vector{Any}", "", "", 0, 3, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Expr", "", "", 0, 2, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.Argument", "", "", 0, 2, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.ReturnNode", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.LineInfoNode", "", "", 0, 2, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Vector{Symbol}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Vector{Int32}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("BufferType", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("sim_t_test##kw", "In[2]", ".\\In[2]", 3, 104, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#sim_t_test#1", "In[2]", ".\\In[2]", 4, 1, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("getindex", "array.jl", ".\\array.jl", 404, 1, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("Array", "boot.jl", ".\\boot.jl", 459, 1, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("Vector{Float64}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[])])])]), ProfileCanvas.ProfileFrame("#sim_t_test#1", "In[2]", ".\\In[2]", 

In [4]:
using Distributions
using Random

function sim_t_test_rev(; dist = Normal(), n = 10, μ = mean(dist), L = 10^5,
        pval = Vector{Float64}(undef, L),
        tmp = Vector{Float64}(undef, n)
    )
    for i in 1:L
        X = rand!(dist, tmp)
        X̄ = mean(X)
        S = std(X)
        t = √n * (X̄ - μ)/S
        pval[i] = 2ccdf(TDist(n-1), abs(t))
    end
    pval
end

n = 10
L = 100
pval =  Vector{Float64}(undef, L)
tmp =  Vector{Float64}(undef, n)
pval = @time sim_t_test_rev(; n, L, pval, tmp)
pval = @time sim_t_test_rev(; n, L, pval, tmp)
pval = @time sim_t_test_rev(; n, L, pval, tmp)
pval = @btime sim_t_test_rev(; n=$n, L=$L, pval=$pval, tmp=$tmp);

  0.037631 seconds (45.87 k allocations: 2.538 MiB, 97.36% compilation time)
  0.000053 seconds (2 allocations: 96 bytes)
  0.000054 seconds (2 allocations: 96 bytes)
  28.900 μs (0 allocations: 0 bytes)


In [5]:
@profview_allocs sim_t_test_rev(; n, L, pval, tmp) sample_rate=1

ProfileCanvas.ProfileData(Dict{String, ProfileCanvas.ProfileFrame}("count" => ProfileCanvas.ProfileFrame("root", "", "", 0, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#15", "task.jl", ".\\task.jl", 484, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eventloop", "eventloop.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\eventloop.jl", 8, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("invokelatest", "essentials.jl", ".\\essentials.jl", 726, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#invokelatest#2", "essentials.jl", ".\\essentials.jl", 729, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("execute_request", "execute_request.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\execute_request.jl", 67, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("softscope_include_string", "SoftGlobalScope.jl", "D:\\.julia\\packages\\SoftGlobalScope\\u4UzH\\src\\SoftGlobalScope.jl", 65, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("include_string", "loading.jl", ".\\loading.jl", 1428, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eval", "boot.jl", ".\\boot.jl", 368, 6, missing, 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("NTuple{4, Symbol}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.SimpleVector", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("DataType", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("UnionAll", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Tuple{Int64, Int64, Vector{Float64}, Vector{Float64}}", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("UnknownType", "", "", 0, 1, missing, 0x02, missing, ProfileCanvas.ProfileFrame[])])])])])])])])])]), "size" => ProfileCanvas.ProfileFrame("root", "", "", 0, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#15", "task.jl", ".\\task.jl", 484, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eventloop", "eventloop.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\eventloop.jl", 8, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("invokelatest", "essentials.jl", ".\\essentials.jl", 726, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("#invokelatest#2", "essentials.jl", ".\\essentials.jl", 729, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("execute_request", "execute_request.jl", "D:\\.julia\\packages\\IJulia\\AQu2H\\src\\execute_request.jl", 67, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("softscope_include_string", "SoftGlobalScope.jl", "D:\\.julia\\packages\\SoftGlobalScope\\u4UzH\\src\\SoftGlobalScope.jl", 65, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("include_string", "loading.jl", ".\\loading.jl", 1428, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("eval", "boot.jl", ".\\boot.jl", 368, 216, "216 bytes", 0x00, missing, ProfileCanvas.ProfileFrame[ProfileCanvas.ProfileFrame("NTuple{4, Symbol}", "", "", 0, 32, "32 bytes", 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("Core.SimpleVector", "", "", 0, 56, "56 bytes", 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("DataType", "", "", 0, 120, "120 bytes", 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCanvas.ProfileFrame("UnionAll", "", "", 0, 136, "136 bytes", 0x02, missing, ProfileCanvas.ProfileFrame[]), ProfileCan

In [6]:
val = @showtime 1 + 2sum(sin(x)/x for x in 1:10^8)
val

1 + 2 * sum((sin(x) / x for x = 1:10 ^ 8)): 2.720984 seconds (357.91 k allocations: 18.300 MiB, 3.61% compilation time)


3.1415926695599605

In [7]:
function sim_t_test_showtime(; dist = Normal(), n = 10, μ = mean(dist), L = 10)
    @showtime pval = Float64[]
    println()
    for i in 1:L
        @show i
        @showtime X = rand(dist, n)
        @showtime X̄ = mean(X)
        @showtime S = std(X)
        @showtime t = √n * (X̄ - μ)/S
        @showtime p = 2ccdf(TDist(n-1), abs(t))
        @showtime push!(pval, p)
        println()
    end
    @showtime pval
end

sim_t_test_showtime();

pval = Float64[]: 0.000003 seconds (1 allocation: 64 bytes)

i = 1
X = rand(dist, n): 0.000004 seconds (1 allocation: 144 bytes)
X̄ = mean(X): 0.000000 seconds
S = std(X): 0.000002 seconds
t = (√n * (X̄ - μ)) / S: 0.000000 seconds
p = 2 * ccdf(TDist(n - 1), abs(t)): 0.000015 seconds
push!(pval, p): 0.000001 seconds (1 allocation: 80 bytes)

i = 2
X = rand(dist, n): 0.000002 seconds (1 allocation: 144 bytes)
X̄ = mean(X): 0.000000 seconds
S = std(X): 0.000001 seconds
t = (√n * (X̄ - μ)) / S: 0.000000 seconds
p = 2 * ccdf(TDist(n - 1), abs(t)): 0.000002 seconds
push!(pval, p): 0.000000 seconds

i = 3
X = rand(dist, n): 0.000002 seconds (1 allocation: 144 bytes)
X̄ = mean(X): 0.000000 seconds
S = std(X): 0.000000 seconds
t = (√n * (X̄ - μ)) / S: 0.000000 seconds
p = 2 * ccdf(TDist(n - 1), abs(t)): 0.000002 seconds
push!(pval, p): 0.000001 seconds

i = 4
X = rand(dist, n): 0.000001 seconds (1 allocation: 144 bytes)
X̄ = mean(X): 0.000000 seconds
S = std(X): 0.000000 seconds
t = (√n * (X̄ -